In [68]:
import pandas as pd
from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler
import plotly.express as px
import hvplot.pandas
from sklearn.decomposition import PCA

In [69]:
team_data = pd.read_csv('/Users/adambachrach/Desktop/Yellow_Project/ml-25m/yellowteam_movie_data.csv')
movie_df = pd.DataFrame(team_data)
movie_df.head()

Unnamed: 0  movieId                               title  \
0           0        1                    Toy Story (1995)   
1           1        2                      Jumanji (1995)   
2           2        3             Grumpier Old Men (1995)   
3           3        4            Waiting to Exhale (1995)   
4           4        5  Father of the Bride Part II (1995)   

                                        genres  imdbId   tmdbId  \
0  Adventure|Animation|Children|Comedy|Fantasy  114709    862.0   
1                   Adventure|Children|Fantasy  113497   8844.0   
2                               Comedy|Romance  113228  15602.0   
3                         Comedy|Drama|Romance  114885  31357.0   
4                                       Comedy  113041  11862.0   

   number of ratings    rating  
0              57309  3.893708  
1              24228  3.251527  
2              11804  3.142028  
3               2523  2.853547  
4              11714  3.058434

In [70]:
genres = []
for i in range(len(movie_df.genres)):
    for x in movie_df.genres[i].split('|'):
        if x not in genres:
            genres.append(x)

for x in genres:
    movie_df[x] = 0
for i in range(len(movie_df.genres)):
    for x in movie_df.genres[i].split('|'):
        movie_df[x][i] = 1

movie_df.drop(['genres'], axis=1)

/var/folders/n9/nmyqjt296k35d4yvkrgc5nbw0000gn/T/ipykernel_51990/1756791645.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movie_df[x][i] = 1


Unnamed: 0  movieId                               title   imdbId  \
0               0        1                    Toy Story (1995)   114709   
1               1        2                      Jumanji (1995)   113497   
2               2        3             Grumpier Old Men (1995)   113228   
3               3        4            Waiting to Exhale (1995)   114885   
4               4        5  Father of the Bride Part II (1995)   113041   
...           ...      ...                                 ...      ...   
59042       59042   209157                           We (2018)  6671244   
59043       59043   209159           Window of the Soul (2001)   297986   
59044       59044   209163                    Bad Poems (2018)  6755366   
59045       59045   209169                 A Girl Thing (2001)   249603   
59046       59046   209171      Women of Devil's Island (1962)    55323   

         tmdbId  number of ratings    rating  Adventure  Animation  Children  \
0         862.0              57309  3.893708          1          1         1   
1        8844.0              24228  3.251527          1          0         1   
2       15602.0              11804  3.142028          0          0         0   
3       31357.0               2523  2.853547          0          0         0   
4       11862.0              11714  3.058434          0          0         0   
...         ...                ...       ...        ...        ...       ...   
59042  499546.0                  1  1.500000          0          0         0   
59043   63407.0                  1  3.000000          0          0         0   
59044  553036.0                  1  4.500000          0          0         0   
59045  162892.0                  1  3.000000          0          0         0   
59046   79513.0                  1  3.000000          1          0         0   

       ...  Horror  Mystery  Sci-Fi  IMAX  Documentary  War  Musical  Western  \
0      ...       0        0       0     0            0    0        0        0   
1      ...       0        0       0     0            0    0        0        0   
2      ...       0        0       0     0            0    0        0        0   
3      ...       0        0       0     0            0    0        0        0   
4      ...       0        0       0     0            0    0        0        0   
...    ...     ...      ...     ...   ...          ...  ...      ...      ...   
59042  ...       0        0       0     0            0    0        0        0   
59043  ...       0        0       0     0            1    0        0        0   
59044  ...       0        0       0     0            0    0        0        0   
59045  ...       0        0       0     0            0    0        0        0   
59046  ...       0        0       0     0            0    0        0        0   

       Film-Noir  (no genres listed)  
0              0                   0  
1              0                   0  
2              0                   0  
3              0                   0  
4              0                   0  
...          ...                 ...  
59042          0                   0  
59043          0                   0  
59044          0                   0  
59045          0                   1  
59046          0                   0  

[59047 rows x 27 columns]

In [71]:
numeric_df = movie_df.drop(['Unnamed: 0', 'movieId', 'title', 'imdbId', 'tmdbId', 'genres'], axis=1)
numeric_df

number of ratings    rating  Adventure  Animation  Children  Comedy  \
0                  57309  3.893708          1          1         1       1   
1                  24228  3.251527          1          0         1       0   
2                  11804  3.142028          0          0         0       1   
3                   2523  2.853547          0          0         0       1   
4                  11714  3.058434          0          0         0       1   
...                  ...       ...        ...        ...       ...     ...   
59042                  1  1.500000          0          0         0       0   
59043                  1  3.000000          0          0         0       0   
59044                  1  4.500000          0          0         0       1   
59045                  1  3.000000          0          0         0       0   
59046                  1  3.000000          1          0         0       0   

       Fantasy  Romance  Drama  Action  ...  Horror  Mystery  Sci-Fi  IMAX  \
0            1        0      0       0  ...       0        0       0     0   
1            1        0      0       0  ...       0        0       0     0   
2            0        1      0       0  ...       0        0       0     0   
3            0        1      1       0  ...       0        0       0     0   
4            0        0      0       0  ...       0        0       0     0   
...        ...      ...    ...     ...  ...     ...      ...     ...   ...   
59042        0        0      1       0  ...       0        0       0     0   
59043        0        0      0       0  ...       0        0       0     0   
59044        0        0      1       0  ...       0        0       0     0   
59045        0        0      0       0  ...       0        0       0     0   
59046        0        0      1       1  ...       0        0       0     0   

       Documentary  War  Musical  Western  Film-Noir  (no genres listed)  
0                0    0        0        0          0                   0  
1                0    0        0        0          0                   0  
2                0    0        0        0          0                   0  
3                0    0        0        0          0                   0  
4                0    0        0        0          0                   0  
...            ...  ...      ...      ...        ...                 ...  
59042            0    0        0        0          0                   0  
59043            1    0        0        0          0                   0  
59044            0    0        0        0          0                   0  
59045            0    0        0        0          0                   1  
59046            0    0        0        0          0                   0  

[59047 rows x 22 columns]

In [72]:
inertia = []
k = list(range(1,11))

for i in k:
    km = KMeans(n_clusters=i, random_state = 0)
    km.fit(numeric_df)
    inertia.append(km.inertia_)

In [73]:
elbow_data = {'k': k, 'inertia': inertia}
df_elbow = pd.DataFrame(elbow_data)
df_elbow.hvplot.line(x='k', y='inertia', title='Elbow Curve', xticks=k)

:Curve   [k]   (inertia)

In [74]:
model = KMeans(n_clusters=4, random_state=0)

model.fit(numeric_df)

predictions = model.predict(numeric_df)

numeric_df['class'] = model.labels_

numeric_df['title'] = movie_df['title']

numeric_df.head()

number of ratings    rating  Adventure  Animation  Children  Comedy  \
0              57309  3.893708          1          1         1       1   
1              24228  3.251527          1          0         1       0   
2              11804  3.142028          0          0         0       1   
3               2523  2.853547          0          0         0       1   
4              11714  3.058434          0          0         0       1   

   Fantasy  Romance  Drama  Action  ...  Sci-Fi  IMAX  Documentary  War  \
0        1        0      0       0  ...       0     0            0    0   
1        1        0      0       0  ...       0     0            0    0   
2        0        1      0       0  ...       0     0            0    0   
3        0        1      1       0  ...       0     0            0    0   
4        0        0      0       0  ...       0     0            0    0   

   Musical  Western  Film-Noir  (no genres listed)  class  \
0        0        0          0                   0      2   
1        0        0          0                   0      1   
2        0        0          0                   0      3   
3        0        0          0                   0      0   
4        0        0          0                   0      3   

                                title  
0                    Toy Story (1995)  
1                      Jumanji (1995)  
2             Grumpier Old Men (1995)  
3            Waiting to Exhale (1995)  
4  Father of the Bride Part II (1995)  

[5 rows x 24 columns]

In [75]:
numeric_df.hvplot.scatter(
    x='rating',
    y='number of ratings',
    hover_cols=['title'],
    by='class'
)

:NdOverlay   [class]
   :Scatter   [rating]   (number of ratings,title)

In [76]:
genome_scores = pd.read_csv('/Users/adambachrach/Desktop/Yellow_Project/ml-25m/genome-scores.csv')
genome_tags = pd.read_csv('/Users/adambachrach/Desktop/Yellow_Project/ml-25m/genome-tags.csv')

In [77]:
genome_scores_df = pd.DataFrame(genome_scores)
genome_tags_df = pd.DataFrame(genome_tags)

In [78]:
genome_tags_scores_df = pd.merge(genome_scores_df, genome_tags_df)
genome_tags_scores_df

movieId  tagId  relevance      tag
0               1      1    0.02875      007
1               2      1    0.04125      007
2               3      1    0.04675      007
3               4      1    0.03425      007
4               5      1    0.04300      007
...           ...    ...        ...      ...
15584443   205072   1128    0.09100  zombies
15584444   205076   1128    0.02350  zombies
15584445   205383   1128    0.03925  zombies
15584446   205425   1128    0.02850  zombies
15584447   206499   1128    0.03350  zombies

[15584448 rows x 4 columns]

In [79]:
full_complete_movie_df = pd.merge(movie_df, genome_tags_scores_df)
full_complete_movie_df

Unnamed: 0  movieId                                title  \
0                  0        1                     Toy Story (1995)   
1                  0        1                     Toy Story (1995)   
2                  0        1                     Toy Story (1995)   
3                  0        1                     Toy Story (1995)   
4                  0        1                     Toy Story (1995)   
...              ...      ...                                  ...   
15584443       58303   206499  Between Two Ferns: The Movie (2019)   
15584444       58303   206499  Between Two Ferns: The Movie (2019)   
15584445       58303   206499  Between Two Ferns: The Movie (2019)   
15584446       58303   206499  Between Two Ferns: The Movie (2019)   
15584447       58303   206499  Between Two Ferns: The Movie (2019)   

                                               genres   imdbId    tmdbId  \
0         Adventure|Animation|Children|Comedy|Fantasy   114709     862.0   
1         Adventure|Animation|Children|Comedy|Fantasy   114709     862.0   
2         Adventure|Animation|Children|Comedy|Fantasy   114709     862.0   
3         Adventure|Animation|Children|Comedy|Fantasy   114709     862.0   
4         Adventure|Animation|Children|Comedy|Fantasy   114709     862.0   
...                                               ...      ...       ...   
15584443                                       Comedy  9398640  584962.0   
15584444                                       Comedy  9398640  584962.0   
15584445                                       Comedy  9398640  584962.0   
15584446                                       Comedy  9398640  584962.0   
15584447                                       Comedy  9398640  584962.0   

          number of ratings    rating  Adventure  Animation  ...  IMAX  \
0                     57309  3.893708          1          1  ...     0   
1                     57309  3.893708          1          1  ...     0   
2                     57309  3.893708          1          1  ...     0   
3                     57309  3.893708          1          1  ...     0   
4                     57309  3.893708          1          1  ...     0   
...                     ...       ...        ...        ...  ...   ...   
15584443                 90  3.055556          0          0  ...     0   
15584444                 90  3.055556          0          0  ...     0   
15584445                 90  3.055556          0          0  ...     0   
15584446                 90  3.055556          0          0  ...     0   
15584447                 90  3.055556          0          0  ...     0   

          Documentary  War  Musical  Western  Film-Noir  (no genres listed)  \
0                   0    0        0        0          0                   0   
1                   0    0        0        0          0                   0   
2                   0    0        0        0          0                   0   
3                   0    0        0        0          0                   0   
4                   0    0        0        0          0                   0   
...               ...  ...      ...      ...        ...                 ...   
15584443            0    0        0        0          0                   0   
15584444            0    0        0        0          0                   0   
15584445            0    0        0        0          0                   0   
15584446            0    0        0        0          0                   0   
15584447            0    0        0        0          0                   0   

          tagId  relevance           tag  
0             1    0.02875           007  
1             2    0.02375  007 (series)  
2             3    0.06250  18th century  
3             4    0.07575         1920s  
4             5    0.14075         1930s  
...         ...        ...           ...  
15584443   1124    0.11000       writing  
15584444   1125    0.04850         wuxia  
15584445   1126    0.01325     

In [80]:
full_complete_movie_df.corr()

Unnamed: 0       movieId        imdbId        tmdbId  \
Unnamed: 0          1.000000e+00  9.689977e-01  8.629797e-01  8.595889e-01   
movieId             9.689977e-01  1.000000e+00  8.387910e-01  8.059351e-01   
imdbId              8.629797e-01  8.387910e-01  1.000000e+00  8.862489e-01   
tmdbId              8.595889e-01  8.059351e-01  8.862489e-01  1.000000e+00   
number of ratings  -1.850553e-01 -1.711074e-01 -1.190504e-01 -1.534667e-01   
rating              6.736116e-02  7.507174e-02  4.244684e-02  2.727268e-02   
Adventure           1.181149e-02  1.915004e-02 -2.601006e-02 -3.352458e-02   
Animation           1.371555e-01  1.489762e-01  6.817043e-02  4.273254e-02   
Children            1.593139e-02  2.215686e-02 -2.277003e-02 -2.919562e-02   
Comedy             -4.152374e-02 -4.128343e-02 -4.692864e-02 -5.513860e-02   
Fantasy             2.958098e-02  3.901390e-02 -8.788762e-03 -2.477180e-02   
Romance            -8.513136e-02 -8.193118e-02 -7.465409e-02 -8.249502e-02   
Drama              -6.286556e-02 -6.217002e-02 -5.324931e-02 -4.804409e-02   
Action              3.707668e-02  4.276206e-02  1.837623e-02 -6.394451e-03   
Crime              -1.467496e-02 -1.445631e-02 -2.549333e-02 -4.257160e-02   
Thriller            4.449392e-02  5.176294e-02  4.474746e-02  1.435765e-02   
Horror              3.537274e-02  3.175287e-02  3.369239e-02  2.661360e-02   
Mystery             8.389964e-03  8.899495e-03 -3.721944e-03 -1.078831e-02   
Sci-Fi              5.624448e-02  5.715032e-02  3.168106e-02  2.952300e-02   
IMAX                2.704173e-02  5.588302e-02  1.417549e-02 -2.228627e-02   
Documentary         5.250434e-02  6.466729e-02  8.520977e-02  6.687950e-02   
War                -4.014997e-02 -4.332056e-02 -5.112541e-02 -4.616990e-02   
Musical            -6.454930e-02 -6.552583e-02 -6.881147e-02 -6.941634e-02   
Western            -3.576820e-02 -4.541080e-02 -3.982350e-02 -2.781561e-02   
Film-Noir          -4.528071e-02 -4.966315e-02 -5.093828e-02 -4.393752e-02   
(no genres listed)  1.247337e-01  1.166608e-01  1.121073e-01  1.505086e-01   
tagId              -1.344955e-13 -1.390078e-13 -1.253172e-13 -1.243651e-13   
relevance           1.727234e-02  1.535521e-02  1.679892e-02  9.736334e-03   

                    number of ratings        rating     Adventure  \
Unnamed: 0              -1.850553e-01  6.736116e-02  1.181149e-02   
movieId                 -1.711074e-01  7.507174e-02  1.915004e-02   
imdbId                  -1.190504e-01  4.244684e-02 -2.601006e-02   
tmdbId                  -1.534667e-01  2.727268e-02 -3.352458e-02   
number of ratings        1.000000e+00  2.023581e-01  1.484733e-01   
rating                   2.023581e-01  1.000000e+00 -4.943412e-02   
Adventure                1.484733e-01 -4.943412e-02  1.000000e+00   
Animation                2.145260e-02  4.523784e-02  2.120476e-01   
Children                 4.015933e-02 -9.505725e-02  2.761450e-01   
Comedy                   8.310470e-03 -1.450675e-01 -2.899458e-02   
Fantasy                  7.009186e-02 -2.782213e-02  2.469227e-01   
Romance                  2.307598e-02  6.332083e-02 -6.280355e-02   
Drama                   -2.822657e-02  2.932586e-01 -1.510427e-01   
Action                   1.407181e-01 -1.249760e-01  2.787458e-01   
Crime                    5.770263e-02  4.484964e-02 -6.954919e-02   
Thriller                 7.421939e-02 -7.122083e-02 -3.464990e-02   
Horror                  -3.841738e-02 -2.497875e-01 -9.096446e-02   
Mystery                  3.378483e-02  3.229954e-02 -3.841785e-02   
Sci-Fi                   1.140662e-01 -1.113246e-01  1.651309e-01   
IMAX                     1.005560e-01  9.048902e-04  1.380808e-01   
Documentary             -6.613940e-02  1.647314e-01 -6.818591e-02   
War                      1.852894e-02  1.005881e-01  2.153862e-02   
Musical                  6.477664e-03  2.396187e-02 -8.222690e-03   
Western                 -8.497039e-04  2.118805e-02  2.729448e-02   
Film-Noir               -3.223598e

In [97]:
genres_df = movie_df[['genres', 'number of ratings', 'rating']]
genres_df.drop('genres', axis=1)
num_genres_df = pd.get_dummies(genres_df)
num_genres_df


number of ratings    rating  genres_(no genres listed)  genres_Action  \
0                  57309  3.893708                          0              0   
1                  24228  3.251527                          0              0   
2                  11804  3.142028                          0              0   
3                   2523  2.853547                          0              0   
4                  11714  3.058434                          0              0   
...                  ...       ...                        ...            ...   
59042                  1  1.500000                          0              0   
59043                  1  3.000000                          0              0   
59044                  1  4.500000                          0              0   
59045                  1  3.000000                          1              0   
59046                  1  3.000000                          0              0   

       genres_Action|Adventure  genres_Action|Adventure|Animation  \
0                            0                                  0   
1                            0                                  0   
2                            0                                  0   
3                            0                                  0   
4                            0                                  0   
...                        ...                                ...   
59042                        0                                  0   
59043                        0                                  0   
59044                        0                                  0   
59045                        0                                  0   
59046                        0                                  0   

       genres_Action|Adventure|Animation|Children  \
0                                               0   
1                                               0   
2                                               0   
3                                               0   
4                                               0   
...                                           ...   
59042                                           0   
59043                                           0   
59044                                           0   
59045                                           0   
59046                                           0   

       genres_Action|Adventure|Animation|Children|Comedy  \
0                                                      0   
1                                                      0   
2                                                      0   
3                                                      0   
4                                                      0   
...                                                  ...   
59042                                                  0   
59043                                                  0   
59044                                                  0   
59045                                                  0   
59046                                                  0   

       genres_Action|Adventure|Animation|Children|Comedy|Fantasy  \
0                                                      0           
1                                                      0           
2                                                      0           
3                                                      0           
4                                                      0           
...                                                  ...           
59042                                                  0           
59043                                                  0           
59044                                                  0           
59045                                                  0           
59046                                                  0           

       genres_Action|Adventure|Animation|C

In [109]:
genres_df.hvplot.scatter(x='genres', y='rating')

:Scatter   [genres]   (rating)

In [100]:
num_genres_df.dtypes

number of ratings              int64
rating                       float64
genres_(no genres listed)      uint8
genres_Action                  uint8
genres_Action|Adventure        uint8
                              ...   
genres_Thriller|War            uint8
genres_Thriller|Western        uint8
genres_War                     uint8
genres_War|Western             uint8
genres_Western                 uint8
Length: 1623, dtype: object

In [114]:
number_ratings_df = movie_df['number of ratings']
number_ratings_df

0        57309
1        24228
2        11804
3         2523
4        11714
         ...  
59042        1
59043        1
59044        1
59045        1
59046        1
Name: number of ratings, Length: 59047, dtype: int64